In [13]:
import pytorch_lightning as pl
import pytorch_lightning.callbacks as pl_callbacks
import torch
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import eq

from eq.catalogs.ANSS_SCEDC_COMBINED import CombinedCatalog

from eq.data import Catalog, InMemoryDataset, Sequence, default_catalogs_dir

In [14]:
catalogs = []
anss = eq.catalogs.ANSS_MultiCatalog(    
    num_sequences=20,
    t_end_days=1*365,
    mag_completeness=4.5,
    minimum_mainshock_mag=6.0,
)
catalogs.append(anss)
scedc = eq.catalogs.SCEDC()
catalogs.append(scedc)
# white = eq.catalogs.White()
# catalogs.append(white)
# qtm = eq.catalogs.QTMSaltonSea()
# catalogs.append(qtm)

Generating the catalog...
Downloading...
train


100%|██████████| 12/12 [00:00<00:00, 150.95it/s]


val


100%|██████████| 4/4 [00:00<00:00, 322.43it/s]


test


100%|██████████| 4/4 [00:00<00:00, 268.74it/s]


Success!
Catalog saved to /home/gcl/RA/jonahk/recast/data/ANSS_MultiCatalog
Loading existing catalog from /home/gcl/RA/jonahk/recast/data/SCEDC.


/home/gcl/RA/jonahk/recast/eq/data/sequence.py:241: UserWarning: Found 1 zero inter-event times in the sequence. This violates fundamental assumptions of TPP models and may lead to incorrect log-likelihood values.
  warnings.warn(


In [15]:
combined_catalog = CombinedCatalog(catalogs)

Loading existing catalog from /home/gcl/RA/jonahk/recast/notebooks/Jonah/combined.
Length of new sequence: 201
New sequence content: tensor([  0.9643,   4.3189,   8.6538,  11.4245,  13.1027,  15.4042,  17.9387,
         22.0256,  22.2077,  23.1243,  24.4229,  27.0344,  28.6901,  29.9853,
         30.3506,  36.5076,  37.3483,  37.4212,  40.1944,  42.1516,  45.2821,
         45.2892,  45.6893,  46.1906,  47.8807,  49.0979,  55.2839,  55.7762,
         56.8571,  61.1213,  67.8981,  68.9914,  73.0629,  74.7571,  77.6140,
         80.1989,  84.1139,  84.1379,  84.1535,  84.2281,  84.3797,  86.6587,
         89.8308,  89.9418,  90.9028,  91.5859,  92.1365,  93.4644,  95.0055,
         96.6565,  97.9907,  98.5233,  99.6856,  99.8652, 101.1901, 104.3752,
        104.3764, 106.2606, 107.6672, 110.5165, 114.1596, 114.2689, 114.8318,
        116.0901, 121.8261, 122.4706, 126.1964, 126.2309, 127.9166, 127.9310,
        133.5390, 133.9085, 134.1205, 134.1445, 135.1711, 139.6780, 139.6788,
        1

/home/gcl/RA/jonahk/recast/eq/data/sequence.py:241: UserWarning: Found 2 zero inter-event times in the sequence. This violates fundamental assumptions of TPP models and may lead to incorrect log-likelihood values.
  warnings.warn(


In [16]:
combined_catalog.combined_info['combined_train'].sequences[202]

Sequence(
  inter_times: [202],
  arrival_times: [201],
  t_start: 2019.58,
  t_end: 2020.481,
  t_nll_start: 2019.58,
  mag: [201],
  mag_bounds: [2],
  mag_nll_bounds: [2]
)

In [17]:
#combined training and val data
combined_train = combined_catalog.combined_info['combined_train'].get_dataloader( batch_size=50, shuffle=True)
combined_val = combined_catalog.combined_info['combined_val'].get_dataloader( batch_size=50, shuffle=True)

#single training data and val data
scedc_train = combined_catalog.combined_info['SCEDC_train'].get_dataloader( batch_size=1, shuffle=True)
# white_train = combined_catalog.combined_info['White_train'].get_dataloader( batch_size=1, shuffle=True)
anss_train = combined_catalog.combined_info['ANSS_MultiCatalog_train'].get_dataloader( batch_size=5, shuffle=True)
scedc_val = combined_catalog.combined_info['SCEDC_val'].get_dataloader( batch_size=1, shuffle=True)
# white_val= combined_catalog.combined_info['White_val'].get_dataloader( batch_size=1, shuffle=True)
anss_val= combined_catalog.combined_info['ANSS_MultiCatalog_val'].get_dataloader( batch_size=5, shuffle=True)

# single catalog test data
scedc_test = combined_catalog.combined_info['SCEDC_test'].get_dataloader( batch_size=1, shuffle=True)
# white_test = combined_catalog.combined_info['White_test'].get_dataloader( batch_size=1, shuffle=True)
anss_test = combined_catalog.combined_info['ANSS_MultiCatalog_test'].get_dataloader( batch_size=5, shuffle=True)

In [20]:
T = combined_catalog.combined_info['combined_train'].sequences[0].t_end
N = np.mean([len(seq) for seq in combined_catalog.combined_info['combined_train'].sequences])
mag_mean = np.mean([combined_catalog.combined_info['combined_train'].sequences[0].mag.mean().item() for seq in combined_catalog.combined_info['combined_train']])
tau_mean = T/N
mag_completness = 0.6

combined_model = eq.models.RecurrentTPP(
    tau_mean = tau_mean,
    learning_rate=1e-3,
)

In [21]:
    # ModelCheckpoints saves the model with the best validation loss
checkpoint = pl_callbacks.ModelCheckpoint(monitor="total_val_loss")

    # EarlyStopping stops training if the validation loss doesn't improve by more than 1e-3 for 20 epochs
early_stopping = pl_callbacks.EarlyStopping(monitor="total_val_loss", patience=10, min_delta=1e-5)

    # RichProgressBar adds a nice and more functional progress bar
progress_bar = pl_callbacks.RichProgressBar()

    # Trainer set up training and validation loops with previous specs
trainer = pl.Trainer(devices=1,max_epochs=1000, callbacks=[checkpoint, early_stopping, progress_bar],log_every_n_steps=1, 
accumulate_grad_batches=20)

trainer.fit(combined_model, combined_train, combined_val)

trainer.test(combined_model, scedc_test)


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2]


┏━━━┳━━━━━━━━━━━━━━━┳━━━━━━━━━┳━━━━━━━━┓
┃   ┃ Name          ┃ Type    ┃ Params ┃
┡━━━╇━━━━━━━━━━━━━━━╇━━━━━━━━━╇━━━━━━━━┩
│ 0 │ hypernet_time │ Linear  │  3.2 K │
│ 1 │ hypernet_mag  │ Linear  │     33 │
│ 2 │ rnn           │ GRU     │  3.5 K │
│ 3 │ dropout       │ Dropout │      0 │
└───┴───────────────┴─────────┴────────┘

Trainable params: 6.7 K                                                                                            
Non-trainable params: 0                                                                                            
Total params: 6.7 K                                                                                                
Total estimated model params size (MB): 0

Output()

/home/gcl/RA/jonahk/miniconda3/envs/DS-discovery/lib/python3.11/site-packages/pytorch_lightning/trainer/connectors/
data_connector.py:490: PossibleUserWarning: Your `val_dataloader`'s sampler has shuffling enabled, it is strongly 
recommended that you turn shuffling off for val/test dataloaders.
  rank_zero_warn(

/home/gcl/RA/jonahk/miniconda3/envs/DS-discovery/lib/python3.11/site-packages/pytorch_lightning/trainer/connectors/
data_connector.py:442: PossibleUserWarning: The dataloader, val_dataloader, does not have many workers which may be
a bottleneck. Consider increasing the value of the `num_workers` argument` (try 64 which is the number of cpus on 
this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(

/home/gcl/RA/jonahk/miniconda3/envs/DS-discovery/lib/python3.11/site-packages/pytorch_lightning/trainer/connectors/
data_connector.py:442: PossibleUserWarning: The dataloader, train_dataloader, does not have many workers which may 
be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 64 which is the number of cpus 
on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(

In [ ]:
T = scedc.train[0].t_end

N = np.mean([len(seq) for seq in scedc.train])
mag_mean = np.mean([scedc.train[0].mag.mean().item() for seq in scedc.train])
tau_mean = T/N

single_model = eq.models.RecurrentTPP(
    mag_mean = mag_mean,
    tau_mean = tau_mean,
    mag_completeness=catalog1.metadata['mag_completeness'],
    learning_rate=1e-3,
)

    # ModelCheckpoints saves the model with the best validation loss
checkpoint = pl_callbacks.ModelCheckpoint(monitor="total_val_loss")

    # EarlyStopping stops training if the validation loss doesn't improve by more than 1e-3 for 20 epochs
early_stopping = pl_callbacks.EarlyStopping(monitor="total_val_loss", patience=10, min_delta=1e-5)

    # RichProgressBar adds a nice and more functional progress bar
progress_bar = pl_callbacks.RichProgressBar()

    # Trainer set up training and validation loops with previous specs
trainer = pl.Trainer(devices=1,max_epochs=1000, callbacks=[checkpoint, early_stopping, progress_bar],log_every_n_steps=1)

trainer.fit(single_model, scedc_train, scedc_val)

trainer.test(single_model, scedc_test)